# Topic analysis based on Genius songs lyrics

Author : lievre.thomas@gmail.com

---

In this notebook, we will explore the genius data extract from [Kaggle](https://www.kaggle.com/datasets/carlosgdcj/genius-song-lyrics-with-language-information).

**The aim of this analysis is to retrieve topic from lyrics and retrieve main topics by year or decade.**

This notebook was carried out in the context of a class project imposed by the [text mining course (TDDE16)](https://www.ida.liu.se/~TDDE16/project.en.shtml) of Linköpings universitet.


## Few informations about Genius website

Genius is an American digital company founded on August 27, 2009, by Tom Lehman, lan Zechory, and Mahbod Moghadam. Originally launched as Rap Genius with a focus on hip-hop music, it was initially a crowdsourced website where people could fill in the lyrics of rap music and give an interpretation of the lyrics. Over the years the site has grown to contain several million annotated texts from all eras ( from [Wikipedia Genius page](https://en.wikipedia.org/wiki/Genius_(company))).


## Load the data in memory

Data are all contain in a big 9GB csv file (around 5 millions rows). It could be difficult to load all this data in our computer memory. To deal with this issue, I made a loading class to split the data in 6 pickles files to improve the compressness of the data which aim to improve the loading speed in the memory. Then the pickles are randomly draw to improve generality of the data. We currently assumed the data pickles batch are identically distributed (we will explore the data batches at the second part). The class below deal with all the process.

In [1]:
import pandas as pd
from random import seed, sample
import pickle
import glob
import os

class Loader():

    def __init__(self, in_path, out_path):
        """
        Args:
            in_path (str): csv input path.
            out_path (str): Output directory path to store the pickles.
            chunksize (int, optional): Chunksize for DataFrame reader. Defaults to 10**6. 
        """

        self.__in_path = in_path
        self.__out_path = out_path
        self.__chunksize = 10**6

    def __produce_pickles(self):
        """produce pickles by reading csv by chunksize
        """
        with pd.read_csv(self.__in_path, chunksize = self.__chunksize) as reader:
            try:
                os.makedirs(self.__out_path)
            except FileExistsError:
                # directory already exists
                pass
            for i, chunk in enumerate(reader):
                out_file = self.__out_path + "/data_{}.pkl".format(i+1)
                with open(out_file, "wb") as f:
                    pickle.dump(chunk, f, pickle.HIGHEST_PROTOCOL)
    
    def load_pickle(self, pickle_id):
        """load a pickle file by id

        Args:
            pickle_id (int): pickle id.

        Raises:
            Exception: The path of the given id isn't a file

        Returns:
            obj: DataFrame
        """
        # produce the pickles if the directory not exists or
        # if the directory is empty 
        if (not os.path.exists(self.__out_path)) or \
              (len(os.listdir(self.__out_path)) == 0):
            self.__produce_pickles()
        
        # get the file path following the pickle_id
        # given in parameter
        file_path = self.__out_path + \
            "/data_" + str(pickle_id) + ".pkl"

        if os.path.isfile(file_path):
            df = pd.read_pickle(file_path)
        else:
            raise Exception("The pickle file data_{}.pkl doesn't exist".format(pickle_id))
        return df
        

    def random_pickles(self, n_pickles = 3, init = 42, verbose = True):
        """random reader over pickles files

        Args:
            n_pickles (int, optional): number of pickles to load. Defaults to 3.
            init (int, optional): Integer given to the random seed. Defaults to 42.
            verbose (bool, optional): Print the loaded files. Defaults to True

        Raises:
            Exception: Stop the process if n_pickles exceed pickle files number.

        Returns:
            obj: pd.Dataframe
        """

        # produce the pickles if the directory not exists or
        # if the directory is empty 
        if (not os.path.exists(self.__out_path)) or \
              (len(os.listdir(self.__out_path)) == 0):
            self.__produce_pickles()

        pickle_files = [name for name in
                        glob.glob(self.__out_path + "/data_*.pkl")]
        # draw p_files        
        seed(init)

        if n_pickles <= 6:
            random_p_files = sample(pickle_files, n_pickles)
        else:
            raise Exception("The parameter n_pickles (" +
                            "{}) exceed the numbers of pickle files ({})"\
                                .format(n_pickles, len(pickle_files)))
        # print the drawed files
        if verbose:
            print("Loaded pickles:")
            for p in random_p_files:
                print(p)

        # load random pickles file
        df_list = [pd.read_pickle(p) for p in random_p_files]

        # create the dataframe by concatenate the previous
        # dataframes list
        df = pd.concat(df_list, ignore_index = True)
        return df

In [2]:
# create reader
#  /!\ change path in kaggle
kaggle_input = "/kaggle/input/genius-song-lyrics-with-language-information/song_lyrics.csv"
kaggle_output = "/kaggle/working/data/"

# initiate the file loader
loader = Loader(in_path = kaggle_input, out_path = kaggle_output)

# load random pickle files
df = loader.random_pickles(n_pickles = 1)

Loaded pickles:
/kaggle/working/data/data_3.pkl


Batchs of data are randomly loaded in the memory. The number of batchs loaded depends on the memory capacity of the computer running the script. For the analysis, we will only works on the random samples loaded (All the data in Kaggle).  

# Exploring the coarse data

Let's visualize and explore the coarse data before a part of deeper analysis.

In [3]:
df.head()

title   tag        artist  year  views               features  \
0           Roses  rock         Vitja  2017    399                     {}   
1  Keep On Pushin   rap       Problem  2017    692  {"My Princess Aeryn"}   
2          Inside   pop  The jepettos  2017   1302                     {}   
3  Girls Like You    rb      PnB Rock  2017  60114                     {}   
4        Froideur   rap   N'Dirty Deh  2017   5813      {"N\\'Dirty Deh"}   

                                              lyrics       id language_cld3  \
0  The roses start to wither\nWhere the devil lay...  3019113            en   
1  [Hook]\nImma keep on pushin\nImma keep on push...  3019114            en   
2  [Intro]\nOoh, ooh, ah, ah (x2)\n\n[Verse 1]\nI...  3019115            en   
3  [Chorus]\nBaby it was real\nYeah we were the b...  3019117            en   
4  [Refrain]\nEt j'ai perdu la foi, mais c'est pa...  3019120            fr   

  language_ft language  
0          en       en  
1          en       en  
2          en       en  
3          en       en  
4          fr       fr

For each songs, we've got several informations :
- title of the song
- the tag (which kind of music)
- the artist singer name
- the release year
- the number of page views
- the featuring artists names
- the lyrics
- the genius identifier
- Lyrics language according to [CLD3](https://github.com/google/cld3). Not reliable results are NaN. CLD3 is a neural network model for language indentification.
- Lyrics language according to [FastText's langid](https://fasttext.cc/docs/en/language-identification.html). Values with low confidence (<0.5) are NaN. FastText's langid is library developped by Facebook’s AI Research lab for efficient learning of word representations and sentence classification. fastText has also published a fast and accurate tool for text-based language identification capable of recognizing more than 170 languages.
- Combines language_cld3 and language_ft. Only has a non NaN entry if they both "agree".

More information at this link : https://www.kaggle.com/datasets/carlosgdcj/genius-song-lyrics-with-language-information

In [4]:
df.dtypes

title            object
tag              object
artist           object
year              int64
views             int64
features         object
lyrics           object
id                int64
language_cld3    object
language_ft      object
language         object
dtype: object

In [5]:
# display the size
print('Data frame size (row x columns):', df.size)
print('Data rows number: ', len(df))
print('Number of unique songs (following genius id): ', len(df.id.unique()))

Data frame size (row x columns): 11000000
Data rows number:  1000000
Number of unique songs (following genius id):  1000000


Genius id seems to be the unique rows identifier.

Let's vizualise size of the coarse data over years before preprocessing to compare batch distributions. One things to know before vizualise the data, the pickles are create by chunks reading. 

The last diplayed table gives us some information about the data. The csv file seems to be sort by id, so the pickle files are then sort too.

In [6]:
import plotly.express as px
import plotly.io as pio

# change theme template for every graph below
pio.templates.default = "plotly_white"


# get some information about the pickle data
def pickle_informations(data = loader):
    rows = []
    for i in range(1, len(os.listdir('data')) + 1):
        df = data.load_pickle(i)
        rows.append(len(df))
        del df
    return rows

# get the rows
rows = pickle_informations()

# create the dataframe
df_data = pd.DataFrame(
    {'batch' : ['data ' + str(i) for i in range(1,len(rows) + 1)],
    'rows' : rows})

fig = px.bar(df_data, x="batch", y="rows")
fig.show()

Batch seems to have the same number of rows rexcept for the last one which is consistent because batch are create iteratively by 10e6 chunks over the csv The last batch could be seen as a rest.

In [7]:
import plotly.graph_objects as go

def add_bar(i, y1, y2, color, data = loader):
    df = data.load_pickle(i)
    df = df[(df.year >= y1) & (df.year <= y2)]
    df_year = df.groupby(['year']).size().reset_index(name='count')
    new_bar = go.Bar(
                x = df_year.year.values,
                y = df_year['count'].values,
                name = 'data_'+ str(i),
                marker = {'color' : color})
    new_trend = go.Scatter(
                x = df_year.year.values,
                y = df_year['count'].values,
                mode="lines",
                line={'color' : color,
                    'width' : 0.5},
                showlegend=False)
    del df_year, df
    return new_bar, new_trend


def multi_barplot(year1, year2, colors):    
    # create a empty plotly.Figure object
    fig = go.Figure() 
    # compute the batch number
    n_batch = len(os.listdir('data'))
    # test the color list feed in argument
    # fit well with the batch number
    if n_batch > len(colors):
        raise Exception(
            "The colors list size({})doesn't ".format(len(colors)) +
            "fit with the number of data".format(n_batch))
    for i in range(1, n_batch + 1):
        fig.add_traces((add_bar(i, year1, year2, colors[i-1])))
    fig.update_layout(
        title = "Data distribution over years ({} - {})"
            .format(year1, year2),
        xaxis_title="years",
        yaxis_title="title",
        legend_title="Data batch")
    return fig


In [8]:
import plotly.colors as col

# create the color list
colors = col.qualitative.Plotly

# 1990 - 2023
fig1 = multi_barplot(1960, 1989, colors)
fig1.show()
# 1960 - 1990
fig2 = multi_barplot(1990, 2023, colors)
fig2.show()

The first bar chart (1960 - 1989) shows an increasing numbers of data over years. Moreover batch seems to have quite similar distriutions over years. data_1 and data_2 batch quite outperform the 4 others. data_6 batch is weaker than the other due to its poor number of rows.
The data behaves similarly until 2012 as we can see on the second chart (1990-2023). After this year there is great increasing of the data retrieved. A minimum increase of at least 100% of the batch can be observed. An increase of up to 50 times the batch size for some.

# Data pre-processing

The aim of this part is to preprocess data in order to get suitable data for the analysis. let's focus on the year variable.

We will focus on English songs, to facilitate the analysis and the work of natural language processing algorithms.

In [9]:
# Retrieve only the texts identified as English language by both cld3 and fasttext langid
df = df[df.language == 'en']

Next, it can be quite interseting to check Nan values

In [10]:
# find which column contain nan value
df.columns[df.isna().any()].tolist()

['title']

In [11]:
# get all rows that contain NaN values
df_nan = df[df.isna().any(axis=1)]
df_nan

title   tag                artist  year  views  \
114245   NaN  rock          Peter Dzubay  2017     52   
146772   NaN   rap                OLlama  2017   2120   
158344   NaN  rock  The Moth & The Flame  2011   1051   
160846   NaN  misc              Lawfermz  2017      3   
210243   NaN   rap        TripleYoThreat  2017     24   
211581   NaN   rap               Huntaps  2017    157   
294150   NaN   rap      Shaiza Maponyaza  2018     45   
309207   NaN  rock                  PAWS  2016    271   
357786   NaN   rap             J4ydizz1e  2018     55   
441948   NaN   rap          Bass Santana  2018   1147   
443704   NaN   rap           Poetic Mind  2018     43   
505748   NaN   rap                 KHANS  2018   1445   
584973   NaN  rock        Kathryn Joseph  2018    495   
619397   NaN   rap          Alex Micheal  2018     18   
643909   NaN   pop                 Kenia  2018     37   
670773   NaN   rap           Mehki Raine  2019    161   
671652   NaN  misc          Yoshi Flower  2018    115   
705033   NaN   pop         Matte SEXWAVE  2018     30   
805070   NaN   rap       Doxthe_maverick  2019     60   
991042   NaN    rb         YoungLamentar  2019     25   
992848   NaN   rap            Patagonist  2016     29   

                             features  \
114245                             {}   
146772                             {}   
158344                             {}   
160846                             {}   
210243                             {}   
211581                             {}   
294150                             {}   
309207                             {}   
357786                             {}   
441948  {"Kin\\$oul","Skott Summerz"}   
443704                             {}   
505748                             {}   
584973                             {}   
619397                             {}   
643909                             {}   
670773                             {}   
671652                             {}   
705033                   {"King Jaf"}   
805070                             {}   
991042                             {}   
992848                             {}   

                                                   lyrics       id  \
114245  When I finally find what's real, why shouldn't...  3166588   
146772  [Intro]\nToo many bitches; Too many bitches tr...  3210807   
158344  We used to be so similar\nWell that was wishfu...  3226446   
160846  (Intro)\nBeep beep beep beep beep beep.\nHello...  3230118   
210243  TripleYoThreat, you ain't never gonna make it\...  3296318   
211581  [Hook]\nFuck 12, if you fuck with me I'll send...  3297867   
294150  [intro]\n\nYah yah yah yah\nYah yah\nMan same ...  3438103   
309207  You're scared of history repeating on me\nCons...  3472732   
357786  [Intro: J4yDiZz1e]\n\nThis shit sounds just li...  3561848   
441948  [Intro: Bass Santana]\nTo Bass be the glory\nF...  3681585   
443704  [Verse 1: Exodu$]\n\nSee it started off when i...  3684185   
505748  Countdown to start...\n\n[Dialogue: "MOONLIGHT...  3777115   
584973  When the winter comes up\nSpring comes down\nW...  3890686   
619397  I can\nI can\nI can tell you how it be round h...  3939140   
643909  (verse 1)\nI try to know what I feel\nI`m stil...  3974045   
670773  [Verse 1]:\nI’m a soldier, man I love the atte...  4013370   
671652  [Interlude: Brandon Wardell]\nHey son, been li...  4014692   
705033  (Chorus) Matte SEXWAVE\n\nDon't be surprised w...  4065090   
805070  [Verse:]\n\nOhh God!\nLook they losing faith i...  4217064   
991042  But girl I love you, I can't kill myself\nStay...  4517608   
992848  Verse 1\n\nI love cyana\nShaniq teanna\nTaylor...  4520528   

       language_cld3 language_ft language  
114245            en          en       en  
146772            en          en       en  
158344            en          en       en  
160846            en          en       en  
210243            en          en       en  
211581            en          en       en  


In [12]:
print('Number of untitled song:', len(df[df.isna().any(axis=1)]))

Number of untitled song: 21


Insofar as the title of the music is not to be taken into account in the learning of the topic modeling algorithms but But the titles can be related to the topics in the next phase of analysis and the low number of songs without any title, I decide to delete this data for the moment.

In [13]:
# Delete rows containing NaN values
df = df.dropna()
len(df)

645573

Next, we also try to check for None values

In [14]:
df[df.isnull().any(axis=1)]

Empty DataFrame
Columns: [title, tag, artist, year, views, features, lyrics, id, language_cld3, language_ft, language]
Index: []

No None values in this dataframe.

Afterwards, let's look at the year variable, which is one of the important variables to take into account in our analysis because we want to extract the topics by decades.

In [15]:
years = df.year.unique()
print(years)

print('Number of unique years: ',len(years))

[2017 2016 1998 2002 2011 2013 2014 2015 2006 2009 2012 2005 2018 2008
 2003 2010 2007 1989 1986 1999 1905 1985 1994 2001 1899 1913 2000 2020
 1990 1984 1983 1979 2021 1995 2004 1825 1992 1993 2019 1980 1977 1966
 1988 1991 1997 1949 1957 1982 1674 1996 1974 1942 1850 1842    1 1964
 1972 1915 1976 1930 1987 1919 1911 1960 1978 1968 1975 1950 1981 1952
 1973 1951 1947 1954 1961 1892 1878 1934 1935 1970 1969 1944 1962 1909
 2022 1971 1927 1945 1936 1926 1938 1901   12 1900 1922 1929 1937 1953
 1820 1864 1965 1955 1540 1916 1963 1967 1918 1904 1943   14 1772 1788
 1780 1959 1886 1939 1871 1912 1956 1958 1880 1923 1910 1844 1897 1914
 1862 1933 1946   15 1877 1771   17 1948 1931 1898 1700 1888 1928  510
 1791 1895 1941 1920   25 1917 1908 1940 1859 1907 1902 2023 1857 1863
 1666 1893 1889 1861 1869 1925 1867 1872 1676 1675  420 1932  709 1818
 1830 1005 1866 1066  176 1300 1924 1251 1838 1760 1739   21 1758 1469
    2 1400 1853 1320 1200 1890 1860 1903   18 1220  130 1794 1896 1461
 1210 

We firstly want to know if the year variable format is suitable. It is highly likely that year are sometimes downsized (example : 92 instead of 1992).
Let's display the tag distribution for music with a release year below 215.

In [16]:
df_tag = df[df['year'] < 215].groupby(['tag']).size().reset_index(name='count')

fig = px.pie(df_tag, names="tag", values="count", title = "Outlier tag distribution")
fig.show()

It is rather surprising to observe that the majority style of music of this period (< 215) is rap music knowing that this style is known for the current emerging style. Of course, among this data their is a important part of outlier year.

In [17]:
# Extract the pieces of music of type 'rap' lower than the year 215
df_rap = df[(df['year'] < 215) & (df['tag'] == 'rap')]
df_rap.sort_values(by='views',ascending=False).head(20)

title  tag                      artist  \
111689                        Issa Snack  rap             Phatboitheceleb   
268205  Oof sandman sans sans diss track  rap                     Squeaky   
218600                    First Day Home  rap                       RetcH   
381769                              Papi  rap                DON-DON (US)   
715072                         Same Love  rap                  Macklemore   
969927          IWroteThisForTaylorSwift  rap                     Vershad   
268744                      I like frisk  rap                     Squeaky   
945081                    Same Lil Bitch  rap              Shayla Gessler   
18947              Dont Blame Me For You  rap             Kids These Days   
431118                           Robocop  rap             videogamedunkey   
871682              I don’t want another  rap                 $inbad (VA)   
720816                     Wont Back Out  rap          Flawless Real Talk   
151876                   The Race Keemix  rap                     Ayo Kee   
336793                       Tenxx Hours  rap                       Tenxx   
192002                              Kami  rap                      2burbo   
323357                             Sauce  rap  LilFlex (The one and only)   
200497             Dolce Lyrics Finished  rap                  Casper TNG   
731159                             Toast  rap    Guwop gumbo X Bando Beej   
189766                  Pimpin Aint Easy  rap               Jackie B (IL)   
438752   Break Your Fucking Neck Part. 2  rap                      YungQC   

        year  views                                           features  \
111689     1   4182                                                 {}   
268205    15   3206                                                 {}   
218600     1   2334                                                 {}   
381769     1   2129                                                 {}   
715072     1   1767                        {"Macklemore & Ryan Lewis"}   
969927     1   1607                                   {"Brooklyn Zoo"}   
268744     1   1186                                     {"Squeaky jr"}   
945081     1   1023                                                 {}   
18947      1    868    {"VIC MENSA","Macie Stewart","Liam Cunningham"}   
431118     1    766                                 {​videogamedunkey}   
871682     1    669                                  {"\\$inbad (VA)"}   
720816     1    669                                            {Freek}   
151876     1    543                                                 {}   
336793     1    416                                                 {}   
192002    17    415                                                 {}   
323357     1    400                                          {3rdKvng}   
200497     1    357                                                 {}   
731159     1    336  {"Guwop gumbo ft Bando Beej","Guwop gumbo X  B...   
189766     1    309                                                 {}   
438752     1    307                                                 {}   

                                                   lyrics       id  \
111689  Chorus: its ya birthday and you know I ain't f...  3163216   
268205  OOF POOF BOOTH LOSE LOOSE MOVE LUKE FRISK WRIS...  3387617   
218600  [Intro]\n\n[Chorus]\nHome, it's my first day h...  3307004   
381769  [INTRO]\nCall me papi\nCall me papi\nLead her\...  3596060   
715072  When I was in the 3rd grade\nI thought that I ...  4080328   
969927  [Intro]\nJake:  Sounds like your sad. Listen, ...  4484444   
268744  Ok, ok, ok, ok, ok, ok, ok, yeah\nI like frisk...  3388825   
945081  Did me dirty, you been fuckin' with the Same L...  4441966   
18947   [Verse 1: Vic Mensa]\nI'm larger than life, ha...  3044399   
431118  Now that I'm a Robocop\n\nNow I'm never gonna ...  3666068   
871682  (Hook)\n\nI'm Cold hearted, And broke/\nI cold...  4323086   
720816  [Intro - Flawl

In [18]:
df_rap[df_rap['artist'] == 'Kanye East']

Empty DataFrame
Columns: [title, tag, artist, year, views, features, lyrics, id, language_cld3, language_ft, language]
Index: []

If we search the release date of this track on google, we can find a release date from 4 May 2021 on the [Genius website](https://genius.com/Kanye-east-the-secrets-of-dababy-lyrics). Given the year that we find in our table and real one, we can assume some issue about the date format (1 instead 2021).

After few research on genius website, the most viewed songs of this above displayed list seems to be released on 2021 but more views decrease harder is the interpretation of date.

Let's check the second most popular tag 'pop' in this retrieve outliers data :

In [19]:
# Extract the pieces of music of type 'rap' lower than the year 215
df_pop = df[(df['year'] < 215) & (df['tag'] == 'pop')]
df_pop.sort_values(by='views',ascending=False).head(20)

title  tag  \
274779                                      Off White  pop   
951623             I dont wanna see you cryin anymore  pop   
495830                       Hello from the Dark Side  pop   
385856                            The Moons Detriment  pop   
635909                             Mostly to Yourself  pop   
433617                                 Come September  pop   
599147                                           Gone  pop   
433630                         The Pursewarden Affair  pop   
318347                                       The Rose  pop   
918072         U cut me off so the cuts r on me now..  pop   
37439                                          Noirse  pop   
879213  Fadl Shaker - Allah Aalam English Translation  pop   
939993                                Nana Rose Remix  pop   
367980            I’m Working on a Road to Glory Land  pop   
949859                                        Freddie  pop   
860863                                         So Low  pop   
991033                                   Take Me Back  pop   
871246                                    Dear Father  pop   
569400                                          Ghost  pop   
644307                                     1000 years  pop   

                             artist  year  views              features  \
274779                 Zach Clayton     1   7894                    {}   
951623                 Adam Melchor     1   7479                    {}   
495830              RoyishGoodLooks    15   7019                    {}   
385856                  Shannon Lay     1   6698                    {}   
635909                    Noah Reid     1   3517                    {}   
433617                Anas Mitchell     1   1244    {"Anaïs Mitchell"}   
599147                 Ella Martine     1    946                    {}   
433630                Anas Mitchell     1    732    {"Anaïs Mitchell"}   
318347                 Common Holly     1    642                    {}   
918072                 Sapphire2001     1    495                    {}   
37439                   Petite Noir    14    461                    {}   
879213  Genius English Translations     1    383                    {}   
939993                     Big kris     1    278                    {}   
367980       The Earls of Leicester     1    266                    {}   
949859                   Ella Clair     1    265                    {}   
860863                Cinematic Pop     1    264     {"Spencer Jones"}   
991033                       Mcrack     1    245                    {}   
871246                 Laura Bretan     1    229                    {}   
569400                       PYNKIE    12    161                    {}   
644307                 Joel McNeely     1    143  {"KT Tunstall",Bleu}   

                                                   lyrics       id  \
274779  Chorus\nSwish on my kicks, off white\nStripes ...  3399877   
951623  [Verse 1]\nI don't wanna see you cryin’ anymor...  4452665   
495830  [Chorus]\nHello from the Dark Side\nI must've ...  3763085   
385856  If I were to know you\nI’d show you all the li...  3603840   
635909  Well it's mostly in the mornin'\nWhen your eye...  3961929   
433617  Autumn's ashes, summer's embers\nOn the sidewa...  3669873   
599147  [Verse 1]\nIt's hard we hurt each other\nTime ...  3910616   
433630  Percy Pursewarden\nOpen up your door\nI haven'...  3669885   
318347  Well I know I was the rose\nBut now I feel lik...  3496110   
918072  I can feel in the air tonight\nSmoke seeping f...  4401036   
37439   Show me your secret\nLet's have a party\nShow ...  3067334   
879213  Only god knows, if I was dreaming, my darling\...  4334911   
939993  90 years old, it's not young but\nGod broke th...  4434139   
367980  [Chorus]\nI’m Working on a road that leads to ...  3576520   
949859  [Verse 1]\nWell Freddie said my life is really...  4449344   
860863  Have you ever been so low?\nYes you had a hear...  4306998   


The titles recovered seem to be for the most part recent sounds, not very popular with a bad indexation of the years.

A case-by-case pre-processing of the data is too tedious compared to the amount of data to be processed. We will only use data with correctly formatted dates.

In [20]:
df = df[(df.year >= 1960) & (df.year < 2023)]
len(df)

642975

We wish to analyze the texts by decade then let's add a decade column.

In [21]:
import math

df['decade'] = df['year'].map(lambda x : int(math.trunc(x / 10) * 10))

df.sort_values(by = 'year').head(20)

title   tag          artist  \
329044                             Darling If I Had You  rock       Bobby Day   
734933  Tonights All Right For Love Bonus Track Version   pop   Elvis Presley   
752292                                    Row Your Boat   pop   The Chipmunks   
374556                      Two Views of a Cadaver Room  misc    Sylvia Plath   
374557                                     The Eye-Mote  misc    Sylvia Plath   
7170                           Extra Sensory Perception   pop  Sheldon Allman   
374558                                 Hardcastle Crags  misc    Sylvia Plath   
374559                                             Faun  misc    Sylvia Plath   
479255                                        Whirlwind    rb  Barrett Strong   
374560                                        Departure  misc    Sylvia Plath   
655765                                  Show Me the Way   pop     Ben E. King   
752290                          Working on the Railroad   pop   The Chipmunks   
752289                          Swing Low Sweet Chariot   pop   The Chipmunks   
752288                                Sing a Goofy Song   pop   The Chipmunks   
752286                  When Johnny Comes Marching Home   pop   The Chipmunks   
752285                                     Swanee River   pop   The Chipmunks   
752284                             I Wish I Had a Horse   pop   The Chipmunks   
374561                                          Lorelei  misc    Sylvia Plath   
752283                                Home on the Range   pop   The Chipmunks   
774932                                    How About Me?   pop    Julie London   

        year  views               features  \
329044  1960    308                     {}   
734933  1960    142                     {}   
752292  1960    261                     {}   
374556  1960   1079                     {}   
374557  1960    453                     {}   
7170    1960    193                     {}   
374558  1960    266                     {}   
374559  1960    329                     {}   
479255  1960    109  {"The Rayber Voices"}   
374560  1960    375                     {}   
655765  1960    707                     {}   
752290  1960     96                     {}   
752289  1960     65                     {}   
752288  1960    201                     {}   
752286  1960    126                     {}   
752285  1960     67                     {}   
752284  1960    304                     {}   
374561  1960    343                     {}   
752283  1960    186                     {}   
774932  1960     58                     {}   

                                                   lyrics       id  \
329044  Darling if I had you, if I had you\nMmh, what ...  3515784   
734933  Hold me tight the moon's so bright\nTonight th...  4111118   
752292  Careful now, fellas, steady\nDon't tip it over...  4136301   
374556  (1)\nThe day she visited the dissecting room\n...  3585530   
374557  Blameless as daylight I stood looking\nAt a fi...  3585531   
7170    We've got extra sensory perception\nIt makes o...  3029810   
374558  Flintlike, her feet struck\nSuch a racket of e...  3585532   
374559  Haunched like a faun, he hooed\nFrom grove of ...  3585533   
479255  You know it hit me (Hit me like whirlwind)\nYo...  3738355   
374560  The figs on the fig tree in the yard are green...  3585534   
655765  [Verse 1]\nIf I had to swim a river\nOr climb ...  3990976   
752290  Ouch!\nOh, careful Simon!\nOw!\nLook where you...  4136300   
752289  Swing low, sweet chariot\nComing for to carry ...  4136299   
752288  Sing a goofy song as you walk along\nRee dee d...  4136298   
752286  Alvin, Simon, Theodore!\nReady?\nMarch!\n\nWhe...  4136296   
752285  Boys, how would ya like to do something southe...  4136295   
752284  Hey guys, how come you're rubbing a rabbit's f...  4136294   
374561  It is no night to drown in:\nA full moon, rive...  3585535   
752283  Ooo\nOh, give me a home where the buffalo r

# Data vizualisation

Let's do some vizualisation to get a better understanding of our data. As we saw on previous distribution graphs over years, more titles have been recorded over the last 2 decades.

In [22]:
# barplot by decade
def barplot_by_decade(df):

    # groupby decade
    df_d = df.groupby(['decade']).size().reset_index(name='count')

    # create the figure
    fig = go.Figure()

    fig.add_bar(
        x=df_d.decade,
        y=df_d['count'],
        showlegend=False)

    fig.add_scatter(
            x=df_d.decade,
            y=df_d["count"],
            mode="markers+lines",
            name="trend",
            showlegend=False)

    fig.update_layout(
            title = "Music release over years",
            xaxis_title="decade",
            yaxis_title="release")
    return fig

# build and display
fig = barplot_by_decade(df)
fig.show()

In [23]:
# compute tag frequencies by decade
df_pies_d = df.groupby(['decade','tag']).size().reset_index(name='count')
df_pies_d[df_pies_d.decade == 1960]

decade      tag  count
0    1960  country    764
1    1960     misc    271
2    1960      pop   2292
3    1960      rap      8
4    1960       rb    704
5    1960     rock    688

In [24]:
from plotly.subplots import make_subplots

# create en make subplot
fig = make_subplots(rows=3, cols=3,
                    specs=[
                        [{'type':'domain'}
                        for i in range(1,4)] for i in range(1,4)
                    ])
decades = df_pies_d.decade.unique().tolist()
for i in range(0,3):
    for k in range(0,3):
        decade = decades[i*3 + k]
        # group by decade
        df_p = df_pies_d[df_pies_d.decade == decade]
        # add figure
        fig.add_trace(go.Pie(labels=df_p.tag, values=df_p['count'], name=decade), i+1, k+1)
        # add annotation
        fig.add_annotation(arg=dict(
            text=decade, x=k*0.375 + 0.125,
            y=-i*0.3927 + 0.90, font_size=10,
            showarrow=False))
        if (i*3 + k) == 6:
            break


# Use `hole` to create a donut-like pie chart
fig.update_traces(hole=.4, hoverinfo="label+percent+name")

fig.update_layout(
    title_text="Tags proportions by decades"
    # Add annotations in the center of the donut pies.
    #annotations=[dict(text=decade, x=k*0.375+0.125, y= -i*0.125+0.90, font_size=10, showarrow=False)
     #           for k, decade in enumerate(decades) for i in range(0,4)]
)
fig.show()

The different pie charts show us an evolution of the different proportions of music styles by decades from 1960 to today. In the sixties the most listed music style is the **pop music**. Then comes an emergence of a rising style: the **rock**. This one increases with the decades until it overtakes the pop music during the decades 90 and 2000. The two styles come to balance thereafter facing the meteoric rise of the most listed genre in our current decade, namely **rap**. The evolution of the proportions recover can give us a rather precise idea of the most popular styles of their times. However, it is important to remember that the data still has some bias, Genius being a crowdsourced tool created during the last decade and at the base only as a lexical translator of rap music, it is normal to find a large amount of data from this period and especially from this style there.

The different pie charts show us an evolution of the different proportions of music styles by decades from 1960 to today. In the sixties the most listed music style is the **pop music**. Then comes an emergence of a rising style: the **rock**. This one increases with the decades until it overtakes the pop music during the decades 90 and 2000. The two styles come to balance thereafter facing the meteoric rise of the most listed genre in our current decade, namely **rap**. The evolution of the proportions recover can give us a rather precise idea of the most popular styles of their times. However, it is important to remember that the data still has some bias, Genius being a crowdsourced tool created during the last decade and at the base only as a lexical translator of rap music, it is normal to find a large amount of data from this period and especially from this style there.## Text preprocessing

After the visualisation part let's focus more on the main data which are the lyrics.

In [25]:
df.iloc[0]["lyrics"]

"The roses start to wither\nWhere the devil lays to sleep\nAnd sorrow seems to be like joy\nWhere dying lights dance on last time\n\nYou had me at hello\nBut I couldn't see right through your twisted soul\nThis was the downfall of us all\n\n(Roses start to wither\nWhere the devil lays to sleep)\n\nToo close to hell\nI can't see\nWhat ate me up from the inside\nToo close to hell\nI will never see\nWhat ate me up from the inside out\n(From the inside out)\n\nI'm caught in a nightmare\nNo chance to make it out alive\nWhy have we left the place\nWhere we found love\nYou had me at hello\nBut I couldn't see right through your twisted soul\nThis was the downfall of us all\n\n(Roses start to wither\nWhere the devil lays to sleep)\n\nToo close to hell\nI can't see\nWhat ate me up from the inside\nToo close to hell\nI will never see\nWhat ate me up from the inside out\n\nSo sing along\nWe are a battle\nSo sing along\nWhy have you forsaken me?\n\nWhy have you forsaken me?\nWhy have you forsaken m

There is many undesirable characters like the line breaker '\n', figures or square, curly and simple brackets. So let's clean this data with regular expressions.

In [26]:
import re
from numpy.random import randint

def clean_text(text):
    # remove \n
    text = text.replace('\n', ' ')
    # remove punctuation
    text = re.sub(r'[,\.!?]', '', text)
    #removing text in square braquet
    text = re.sub(r'\[.*?\]', ' ', text)
    #removing numbers
    text = re.sub(r'\w*\d\w*',' ', text)
    #removing bracket
    text = re.sub(r'[()]', ' ', text)
    # convert all words in lower case
    text = text.lower()
    return text

# get the results of data cleaning
cleaned_text = df["lyrics"].apply(clean_text)

In [27]:
docs = cleaned_text.to_list()
docs[0]

"the roses start to wither where the devil lays to sleep and sorrow seems to be like joy where dying lights dance on last time  you had me at hello but i couldn't see right through your twisted soul this was the downfall of us all   roses start to wither where the devil lays to sleep   too close to hell i can't see what ate me up from the inside too close to hell i will never see what ate me up from the inside out  from the inside out   i'm caught in a nightmare no chance to make it out alive why have we left the place where we found love you had me at hello but i couldn't see right through your twisted soul this was the downfall of us all   roses start to wither where the devil lays to sleep   too close to hell i can't see what ate me up from the inside too close to hell i will never see what ate me up from the inside out  so sing along we are a battle so sing along why have you forsaken me  why have you forsaken me why have you forsaken me why have you forsaken me why have you forsak

In [28]:
# update dataframe
df.update(cleaned_text)
df.head(3)

title   tag        artist  year  views               features  \
0           Roses  rock         Vitja  2017    399                     {}   
1  Keep On Pushin   rap       Problem  2017    692  {"My Princess Aeryn"}   
2          Inside   pop  The jepettos  2017   1302                     {}   

                                              lyrics       id language_cld3  \
0  the roses start to wither where the devil lays...  3019113            en   
1    imma keep on pushin imma keep on pushin stay...  3019114            en   
2    ooh ooh ah ah        i heard you were the wo...  3019115            en   

  language_ft language  decade  
0          en       en    2010  
1          en       en    2010  
2          en       en    2010

That's better! The libraries that we will use later to perform topic modeling usually provide preprocessing but it is always good to have control over what we manipulate.

# Topic modeling

- [LDA (latent dirichlet allocation)](https://fr.wikipedia.org/wiki/Allocation_de_Dirichlet_latente) are the common way to do topic modeling in the few last years, it works and it's quite easy to use with common python library like [Gensim](https://radimrehurek.com/gensim/auto_examples/index.html).
- [BERTopic](https://maartengr.github.io/BERTopic/index.html) seems to be one of the best technic this day to perform topic modeling. It combine the leverage of [BERT](https://en.wikipedia.org/wiki/BERT_(language_model)) the famous language model with [c-TF-IDF](https://maartengr.github.io/BERTopic/api/ctfidf.html) tansformer.

In order to reach my first dead line (17/03/2023), I didn't have enough time to run BerTopic algorithm.


## Define default tokenizer and Lemmatizer

In [29]:
import spacy

print("set gpu: ", spacy.prefer_gpu())

# small model /!\ take the bigger one for Kaggle
new_nlp = spacy.load('en_core_web_sm')

set gpu:  False


It could be difficult to process all this data on my computer or Kaggle. The memory will quickly be overwhelmed. I will work with a sample of our previously load data in order to avoid memory overload.

In [30]:
from collections import Counter

def sample(balanced = True, data = df, prop = 0.1):
    if balanced:
        # compute the sorted decreasing parties frequencies
        decade_frequencies = Counter(data['decade']).most_common()
        print(decade_frequencies)

        # retrieve the under represented class
        nb_under_class = decade_frequencies[-1][1]

        # Return a random sample of items from each party following the under sampled number of class
        sample_df = data.groupby("decade").sample(n = nb_under_class, random_state = 500)
    else:
        # create sample df 1/3 of the actual loaded data
        sample_df = df.sample(frac = prop)
    return sample_df
        

In [31]:
# sample the data
sdf = sample()

[(2010, 571574), (2000, 33998), (1990, 14189), (1980, 8788), (1970, 7088), (1960, 4727), (2020, 2611)]


In [32]:
# check the distribution of the sample
barplot_by_decade(sdf)

In [33]:
# default preprocessing
def preprocess(text, nlp = new_nlp):

    #TOKENISATION
    tokens =[]
    for token in nlp(text):
        tokens.append(token)

    #REMOVING STOP WORDS
    spacy_stopwords = new_nlp.Defaults.stop_words
    sentence =  [word for word in tokens if word.text.isalpha() and word.text not in spacy_stopwords]

    #LEMMATISATION
    sentence = [word.lemma_ for word in sentence]

    return sentence

## Vizualise most frequent words over decades

In [34]:
from tqdm import tqdm
from sklearn.feature_extraction.text import CountVectorizer

class TermsDocumentsMatrix():
    
    def __init__(self, sdf, decades=[1960, 1970], colorscale = 'Plotly3'):
        # vectorizer on the sample lyrics
        self.__vectorizer = CountVectorizer(tokenizer = preprocess)
        # fit and transform the data
        self.__data_vectorized = self.__vectorizer.fit_transform(
            tqdm(sdf['lyrics'].loc[sdf['decade'].isin(decades)])
        )
        # get decades informations
        self.__decades = sdf['decade'].loc[sdf['decade'].isin(decades)].reset_index(drop=True)
        self.__unique_decades = decades
        # get colorscale template
        self.__colorscale = colorscale
    
    def get_tdmatrix(self):
        
        # compute a Matrix terms document by decades
        df_bw = pd.DataFrame(self.__data_vectorized.toarray(),
                    columns = self.__vectorizer.get_feature_names_out())
        
        # check the length
        if len(df_bw) != len(self.__decades):
            raise Exception('Not the same size')
        
        # concatenate decade
        df_bw['decade'] = self.__decades
        
        # check NaN values
        if len(df_bw.columns[df_bw.isna().any()].tolist()) != 0:
            raise Exception('Decade got Nan values')

        return df_bw
    
    def get_tdm_by_decade(self, decade):
        
        if decade not in self.__unique_decades:
            raise Exception("{} doesn't appear in the decades list".format(decade))
        
        # compute a Matrix terms document by decades (bag of words format)
        df_bw = pd.DataFrame(self.__data_vectorized.toarray(),
                    columns = self.__vectorizer.get_feature_names_out())
        
        # check the length
        if len(df_bw) != len(self.__decades):
            raise Exception('Not the same size')
        
        # concatenate decade
        df_bw['decade'] = self.__decades
        
        # check NaN values
        if len(df_bw.columns[df_bw.isna().any()].tolist()) != 0:
            raise Exception('Decade got Nan values')
        
        # select suitable decade
        df_bw = df_bw[df_bw['decade'] == decade]
        
        return df_bw
    
    def most_freq_terms(self, n_rows = 1, n_cols = 2, n_terms = 10):
        
        # create the document terms matrix
        df_bw = self.get_tdmatrix()
        
        # create en make subplot
        fig = make_subplots(rows=n_rows, cols=n_cols,
                            x_title = 'number of occurrences',
                            y_title = 'terms',
                            subplot_titles = self.__unique_decades)
        
        for i in range(0,n_rows):
            for k in range(0,n_cols):
                if (i*n_rows + k) == len(self.__unique_decades):
                    break
                
                # get the decade
                decade = self.__unique_decades[i*n_rows + k]
            
                #select the suitable decade and delete decade column
                df_decade = df_bw.loc[df_bw.decade == decade, df_bw.columns != 'decade']
                
                # compute terms frequencies by decade
                terms_freq = df_decade.sum().sort_values(ascending = False)
            
                # total number of terms occurences
                total_terms = terms_freq.values
                
                # add figure
                fig.add_trace(go.Bar(y=terms_freq.index.tolist()[:n_terms][::-1],
                                     x=total_terms[:n_terms][::-1],
                                     name=decade,
                                     orientation='h', showlegend = False,
                                    marker = dict(color = total_terms,
                                                  colorscale=self.__colorscale)),
                              i+1, k+1)
        return fig

In [35]:
# first decades
tdm = TermsDocumentsMatrix(sdf, decades = [1960, 1970, 1980, 1990],
                           colorscale = 'Plasma')

# display bar charts of most frequent terms
tdm.most_freq_terms(n_rows = 2, n_cols = 2, n_terms = 15)

100%|██████████| 10444/10444 [07:56<00:00, 21.91it/s]


According to the bar graphs displayed above, a group of words seems to recur on each decade: Love, know, go, feel ... Words that seem to relate to the popular song that can talk about love. This is consistent with our previous analysis from the pie charts showing the proportions of musical styles across time. We also notice an important presence of onomatopoeia like yeah or oh.

In [36]:
# first decades
tdm = TermsDocumentsMatrix(sdf, decades = [2000, 2010, 2020],
                          colorscale = 'Plasma')

# most frequent terms
tdm.most_freq_terms(n_rows = 2, n_cols = 2, n_terms = 15)

100%|██████████| 7833/7833 [07:15<00:00, 17.99it/s]


We get similar results on this second decade with similar high occurrence words. We see a greater amount of onomatopoeia in the current decade. We can explain this by an emergence of the rap music style on this current and last decade. There is in this style of music a very used process, the 'ad-libs'. They are sounds, words or onomatopoeias that the artists pronounce sometimes between two verses or at the end of a sentence to give more impact to their text and to dynamize the atmosphere of a title. This may explain the greater presence of onomatopoeia in the lyrics of this decade.


## Topic modeling with LDA

LDA is a common technic use in topic modeling, we firstly process basic preprocessing.

In [37]:
# gensim
from gensim.models import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.models.ldamulticore import LdaMulticore
from gensim.corpora.dictionary import Dictionary
from gensim.test.utils import datapath

# utils
from datetime import datetime
import logging

# dashboards
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt

# TSNE dependencies
from sklearn.manifold import TSNE
from bokeh.plotting import figure, output_file, show
from bokeh.models import Label
from bokeh.io import output_notebook
import numpy as np
import matplotlib.colors as mcolors

#gensim_log = '/kaggle/working/log/gensim.log'

#initiate log file
#logging.basicConfig(filename=gensim_log,
#                   format='%(asctime)s:%(levelname)s:%(message)s',
#                    level=logging.INFO,
#                   force = True)

# utils
def parse_logfile(path_log):
    matcher = re.compile(r'(-*\d+\.\d+) per-word .* (\d+\.\d+) perplexity')
    likelihoods = []
    with open(path_log) as source:
        for line in source:
            match = matcher.search(line)
            if match:
                likelihoods.append(float(match.group(1)))
    return likelihoods


class LDATopicModeling():
    
    def __init__(self, df = sdf,
                 decade = 1960,
                 directory = "/kaggle/working/models/",
                 existing = False,
                 n_topics = 10,
                 worker_nodes = None,
                lang_preprocess = preprocess,
                cross_valid = False,
                epochs = 30):
        # Apply preprocessing on decade data
        self.__documents = df.loc[df.decade == decade, 'lyrics'].apply(lang_preprocess)
            
        # Create a corpus from a list of texts
        self.__id2word = Dictionary(self.__documents.tolist())
        self.__corpus = [self.__id2word.doc2bow(doc) for doc in self.__documents.tolist()]
        
        #training
        if os.path.isfile(existing):
            # Load a potentially pretrained model from disk.
            self.model = LdaModel.load(temp_file)
            self.__cv_results = None # no cross_valid
            self.__n_topics = n_topics
        elif not cross_valid:
            self.model = LdaMulticore(
                corpus=tqdm(self.__corpus),
                id2word=self.__id2word,
                num_topics=n_topics,
                workers=worker_nodes,
                passes=epochs)
            self.__n_topics = n_topics
            self.__cv_results = None
        else: # cross validation
            
            # hyperparameter
            alpha = []#np.arange(0.01, 1, 0.3).tolist()
            alpha.append('symmetric')
            alpha.append('asymmetric')
            
            # hyperparameter
            eta = []#np.arange(0.01, 1, 0.3).tolist()
            eta.append('symmetric')
            
            # compute results of the cross_validation
            cv_results = {
                 'topics': [],
                 'alpha': [],
                 'eta': [],
                 'coherence': []
            }
            
            # topic range
            topic_range = range(2, n_topics+1)
            
            # prevent the computation time
            total=(len(eta)*len(alpha)*len(topic_range))
            print("total lda computation: ",total)
            model_list = []
            
            for k in topic_range:
                for a in alpha:
                    for e in eta:
                        
                        # train the model
                        model = LdaMulticore(
                            corpus=self.__corpus,
                            id2word=self.__id2word,
                            num_topics=k,
                            workers=worker_nodes,
                            passes=epochs,
                            alpha=a,
                            eta=e)
                        
                        # compute coherence
                        cv = CoherenceModel(
                            model=model,
                            texts=self.__documents,
                            dictionary=self.__id2word,
                            coherence='c_v')
                        
                        print('coherence: {}\nalpha: {}\neta: {}\ntopic: {}'.format(
                            cv.get_coherence(), a, e, k))
                        
                         # Save the model results
                        cv_results['topics'].append(k)
                        cv_results['alpha'].append(a)
                        cv_results['eta'].append(e)
                        cv_results['coherence'].append(cv.get_coherence())
                        model_list.append(model)
            # retrieve index of the highest coherence model
            best_index = np.argmax(cv_results['coherence'])
            
            # choose the model given the best coherence
            self.model = model_list[best_index]
            
            # save results as attribute
            self.__cv_results = cv_results
            
            self.__n_topics = cv_results['topics'][best_index]
                                    
            # logging doesn't work on Kaggle
            #self.__likelihood = parse_logfile()
        # directory path
        self.__directory = directory
    
    # getters
    @property
    def get_id2word(self):
        return self.__id2word
    
    @property
    def get_corpus(self):
        return self.__corpus
    
    @property
    def get_likelihood(self):
        return self.__likelihood
    
    @property
    def get_cv_results(self):
        return pd.DataFrame(self.__cv_results) if self.__cv_results else None
    
    def plot_coherence(self, metric = 'alpha'):
        """metric(str): alpha or eta
        """
        if self.__cv_results is None:
            raise Exception('No cross validation available')
        
        # get the dataframe
        df_res = self.get_cv_results
                                    
        # groupby by metric
        grouped = df_res.groupby(metric)
        # create the layout
        fig = go.Figure()
        for level, df in grouped:
            fig.add_trace(
                go.Scatter(
                    x=df.topics,
                    y=df.coherence,
                    mode='lines+markers',
                    name=str(level)
                )
            )
        fig.update_layout(
            title = "coherence over topics by",
            xaxis_title="topic",
            yaxis_title="coherence")
        return fig
                                    
                                    
    def save_current_model(self):
        # retrieve time
        now = datetime.now()
        # create the directory if it doesn't exist
        try:
            os.makedirs(directory + now.strftime("%d%m%Y_%H%M%S"))
        except:
            pass
        # Save model to disk.
        temp_file = datapath(directory + now.strftime("%d%m%Y_%H%M%S") + '/model')
        
        self.model.save(temp_file)

    def get_perplexity(self):
        return self.model.log_perplexity(self.__corpus)
    
    def get_coherence(self):
        coherence_model_lda = CoherenceModel(
            model=self.model,
            texts=self.__documents,
            dictionary=self.__id2word,
            coherence='c_v')
        return coherence_model_lda.get_coherence()
    
    
    # data vizualisation
    def dashboard_LDAvis(self):
        # some basic dataviz
        pyLDAvis.enable_notebook()
        vis = pyLDAvis.gensim.prepare(self.model, self.__corpus,
                                      dictionary = self.model.id2word)
        return vis
        
    def plot_tsne(self):
        # n-1 rows each is a vector with i-1 posisitons, where n the number of documents
        # i the topic number and tmp[i] = probability of topic i
        topic_weights = []
        for row_list in self.model[self.get_corpus]:
            tmp = np.zeros(self.__n_topics)
            for i, w in row_list:
                tmp[i] = w
            topic_weights.append(tmp)


        # Array of topic weights    
        arr = pd.DataFrame(topic_weights).fillna(0).values

        # Keep the well separated points (optional)
        arr = arr[np.amax(arr, axis=1) > 0.35]

        # Dominant topic number in each doc
        topic_num = np.argmax(arr, axis=1)

        # tSNE Dimension Reduction
        tsne_model = TSNE(n_components=2, verbose=1, init='pca')
        tsne_lda = tsne_model.fit_transform(arr)

        # Plot the Topic Clusters using Bokeh
        output_notebook()
        mycolors = np.array([color for name, color in mcolors.TABLEAU_COLORS.items()])
        plot = figure(title="t-SNE Clustering of {} LDA Topics".format(self.__n_topics), 
                      plot_width=900, plot_height=700)
        plot.scatter(x=tsne_lda[:,0], y=tsne_lda[:,1], color=mycolors[topic_num])
        show(plot)
        
    def plot_likelihood(self):
        fig = go.Figure(
            go.Scatter(x=[range(0,50)], y=self.__likelihood[-50:],
                       mode='lines',
                       name='lines'))
        fig.update_layout(
            title = "Likelihood over passes",
            xaxis_title="Likekihood",
            yaxis_title="passes")
        return fig

In [38]:
# create my model
lda_model = LDATopicModeling()

100%|██████████| 2611/2611 [00:00<00:00, 8332.12it/s]


In [39]:
# print the result
lda_model.model.print_topics()

[(0,
  '0.018*"like" + 0.009*"boy" + 0.008*"beautiful" + 0.008*"world" + 0.008*"kid" + 0.008*"eye" + 0.007*"hand" + 0.007*"place" + 0.006*"look" + 0.006*"old"'),
 (1,
  '0.014*"come" + 0.008*"day" + 0.008*"like" + 0.007*"night" + 0.007*"away" + 0.007*"eye" + 0.007*"know" + 0.006*"da" + 0.006*"rain" + 0.006*"feel"'),
 (2,
  '0.060*"get" + 0.049*"yeah" + 0.039*"to" + 0.026*"go" + 0.019*"ooh" + 0.018*"man" + 0.016*"hey" + 0.011*"girl" + 0.010*"alright" + 0.010*"know"'),
 (3,
  '0.016*"say" + 0.011*"jem" + 0.011*"black" + 0.010*"man" + 0.009*"like" + 0.008*"know" + 0.008*"go" + 0.007*"come" + 0.006*"high" + 0.006*"day"'),
 (4,
  '0.022*"people" + 0.017*"man" + 0.009*"sun" + 0.008*"country" + 0.008*"world" + 0.007*"time" + 0.007*"grow" + 0.007*"good" + 0.006*"sing" + 0.006*"know"'),
 (5,
  '0.035*"ba" + 0.026*"oh" + 0.026*"doo" + 0.022*"love" + 0.019*"ha" + 0.012*"come" + 0.011*"like" + 0.009*"ah" + 0.008*"doont" + 0.008*"fall"'),
 (6,
  '0.028*"go" + 0.028*"come" + 0.022*"old" + 0.020*"hom

In [40]:
lda_model.plot_tsne()

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2559 samples in 0.003s...
[t-SNE] Computed neighbors for 2559 samples in 0.160s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2559
[t-SNE] Computed conditional probabilities for sample 2000 / 2559
[t-SNE] Computed conditional probabilities for sample 2559 / 2559
[t-SNE] Mean sigma: 0.002030


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 65.096115
[t-SNE] KL divergence after 1000 iterations: 0.568872


Loading BokehJS ...

In [41]:
lda_model.dashboard_LDAvis()

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
7      0.149249  0.024065       1        1  35.534561
1     -0.066691  0.032792       2        1  11.297950
3     -0.054275 -0.071161       3        1   9.606184
2      0.136336 -0.051361       4        1   8.539746
6      0.033600 -0.015324       5        1   7.841267
9      0.062210 -0.039831       6        1   7.495367
4     -0.107321 -0.081412       7        1   7.110166
8      0.010637 -0.033879       8        1   4.411383
0     -0.158641  0.015917       9        1   4.158212
5     -0.005103  0.220193      10        1   4.005165, topic_info=     Term         Freq        Total Category  logprob  loglift
8    love  6085.000000  6085.000000  Default  30.0000  30.0000
13   yeah  1942.000000  1942.000000  Default  29.0000  29.0000
51    get  2424.000000  2424.000000  Default  28.0000  28.0000
613    la   756.000000   756.000000  Default  27.0000  27.0000
16   baby  3234.000000  3234.000000  Default  26.0000  26.0000
..    ...          ...          ...      ...      ...      ...
58   know    66.427981  3778.388458  Topic10  -4.9269  -0.8233
61    man    55.749981  1485.246308  Topic10  -5.1021  -0.0649
197  tell    53.443791  1564.600295  Topic10  -5.1444  -0.1592
114  soul    36.908209   247.916726  Topic10  -5.5146   1.3129
154  time    42.902160  1923.075059  Topic10  -5.3641  -0.5852

[766 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
8850      6  0.896994     aa
2972      1  0.033270   aaah
2972      4  0.033270   aaah
2972      6  0.831751   aaah
2972      8  0.033270   aaah
...     ...       ...    ...
733       7  0.120785  young
733       8  0.047264  young
733       9  0.036761  young
733      10  0.236318  young
4897      8  0.898259   zone

[2362 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[8, 2, 4, 3, 7, 10, 5, 9, 1, 6])

Let's perform lda for each decade.

In [42]:
# LDA Topic Modeling by decade
class LDAPipeline():
    
    def __init__(self,
                 prep = preprocess,
                 cv = False,
                 decades = [
        1960, 1970, 1980, 1990, 2000, 2010, 2020
    ]):
        self.models = {
            decade : LDATopicModeling(
                decade = decade,
                lang_preprocess = prep,
                epochs = 10,
                cross_valid = cv) for decade in decades}
        
    def get_metrics(self):
        # compute metrics
        metrics = {
                 'decade': [],
                 'coherence': [],
                 'perplexity': []
        }
        for decade, model in self.models.items():
            metrics['decade'].append(decade)
            metrics['coherence'].append(model.get_coherence())
            metrics['perplexity'].append(model.get_perplexity())
        # create the dataframe
        df_m = pd.DataFrame(metrics)
        df_m.set_index('decade')
        return df_m
        
        
    def lda_info(self, decade):
        lda_model = self.models[decade]

        print("Perplexity: ", lda_model.get_perplexity())
        print("Coherence: ", lda_model.get_coherence())
        lda_model.plot_tsne()
        return lda_model.dashboard_LDAvis()

In [43]:
lda_models = LDAPipeline()

100%|██████████| 2611/2611 [00:00<00:00, 7051.72it/s]


In [44]:
lda_models.get_metrics()

decade  coherence  perplexity
0    1960   0.329869   -7.088129
1    1970   0.376439   -6.910997
2    1980   0.340456   -7.147417
3    1990   0.365702   -7.623511
4    2000   0.347217   -7.724904
5    2010   0.355117   -7.521929
6    2020   0.314070   -7.414439

Display information for each decade.

In [45]:
lda_1960 = lda_models.lda_info(1960)

Perplexity:  -7.0881167495962565
Coherence:  0.3298689799609975


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2583 samples in 0.003s...
[t-SNE] Computed neighbors for 2583 samples in 0.171s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2583
[t-SNE] Computed conditional probabilities for sample 2000 / 2583
[t-SNE] Computed conditional probabilities for sample 2583 / 2583
[t-SNE] Mean sigma: 0.002260


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 64.020584
[t-SNE] KL divergence after 1000 iterations: 0.533557


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [46]:
lda_1960

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5     -0.133683 -0.033692       1        1  27.867085
0     -0.008745 -0.044438       2        1  12.358074
2      0.115549 -0.059766       3        1  11.431475
6     -0.137421  0.016513       4        1   9.630447
4     -0.088299  0.037862       5        1   8.723350
3      0.016666  0.000860       6        1   7.298953
7      0.023299  0.005210       7        1   6.977278
9      0.022289 -0.038369       8        1   6.562195
8      0.106867 -0.056581       9        1   5.527379
1      0.083479  0.172401      10        1   3.623762, topic_info=     Term         Freq        Total Category  logprob  loglift
8    love  6256.000000  6256.000000  Default  30.0000  30.0000
613    la   699.000000   699.000000  Default  29.0000  29.0000
16   baby  3271.000000  3271.000000  Default  28.0000  28.0000
32     oh  3235.000000  3235.000000  Default  27.0000  27.0000
13   yeah  1915.000000  1915.000000  Default  26.0000  26.0000
..    ...          ...          ...      ...      ...      ...
12    way    44.031330  1462.429124  Topic10  -5.2380  -0.1853
96   feel    40.529268  1084.847030  Topic10  -5.3209   0.0305
53     go    41.947621  2579.012726  Topic10  -5.2865  -0.8011
61    man    38.912060  1478.941672  Topic10  -5.3616  -0.3201
51    get    37.853314  2429.664089  Topic10  -5.3892  -0.8441

[784 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
12046     10  0.975872  abilene
3888       2  0.931407    adieu
1615       3  0.948684   africa
1616       3  0.975975  african
1618       3  0.876874     afro
...      ...       ...      ...
203       10  0.012401      yes
9446       5  0.932626   yippie
5472       5  0.924669    yodel
4897       4  0.972414     zone
11574      2  0.905372       zu

[2480 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 1, 3, 7, 5, 4, 8, 10, 9, 2])

In [47]:
lda_1970 = lda_models.lda_info(1970)

Perplexity:  -6.911019454540611
Coherence:  0.37643906363424773


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2561 samples in 0.003s...
[t-SNE] Computed neighbors for 2561 samples in 0.143s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2561
[t-SNE] Computed conditional probabilities for sample 2000 / 2561
[t-SNE] Computed conditional probabilities for sample 2561 / 2561
[t-SNE] Mean sigma: 0.004091


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 64.417763
[t-SNE] KL divergence after 1000 iterations: 0.562608


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [48]:
lda_1970

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.086688 -0.012717       1        1  21.971684
0     -0.011381  0.026761       2        1  14.661404
8     -0.055610  0.056665       3        1  11.188856
5     -0.061720  0.054833       4        1  10.898429
2      0.030146  0.005380       5        1  10.175982
6     -0.105094 -0.071816       6        1   7.022028
9      0.047865 -0.142967       7        1   6.716418
3      0.088637 -0.060973       8        1   6.687186
4      0.031840  0.082016       9        1   6.218080
7      0.122005  0.062818      10        1   4.459933, topic_info=     Term         Freq        Total Category  logprob  loglift
160  love  7127.000000  7127.000000  Default  30.0000  30.0000
569    la  1193.000000  1193.000000  Default  29.0000  29.0000
281  baby  2947.000000  2947.000000  Default  28.0000  28.0000
745   ooh  1180.000000  1180.000000  Default  27.0000  27.0000
247  yeah  2785.000000  2785.000000  Default  26.0000  26.0000
..    ...          ...          ...      ...      ...      ...
14   look    48.663987  1156.362610  Topic10  -5.4119  -0.0581
204   say    48.698600  1209.113065  Topic10  -5.4112  -0.1020
281  baby    48.809217  2947.077391  Topic10  -5.4089  -0.9906
324  will    44.562871   778.876138  Topic10  -5.5000   0.2491
443  mind    44.361968   871.683061  Topic10  -5.5045   0.1320

[782 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
3566     10  0.790024       aaahh
9554      7  0.930017  additional
8605     10  0.887736   aeroplane
6573      5  0.913554         aey
656       1  0.748384      affair
...     ...       ...         ...
1474     10  0.014856       young
9118      2  0.963970         yum
5390      4  0.045469         zip
5390      7  0.022735         zip
5390      8  0.909390         zip

[2534 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1, 9, 6, 3, 7, 10, 4, 5, 8])

In [49]:
lda_1980 = lda_models.lda_info(1980)

Perplexity:  -7.147405795966036
Coherence:  0.3404558179325016


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2575 samples in 0.003s...
[t-SNE] Computed neighbors for 2575 samples in 0.149s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2575
[t-SNE] Computed conditional probabilities for sample 2000 / 2575
[t-SNE] Computed conditional probabilities for sample 2575 / 2575
[t-SNE] Mean sigma: 0.001304


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 62.431847
[t-SNE] KL divergence after 1000 iterations: 0.506097


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [50]:
lda_1980

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2      0.114466  0.047067       1        1  27.753144
0      0.007384 -0.003753       2        1  14.910227
4     -0.042877 -0.007226       3        1  13.027178
8      0.042927  0.008189       4        1   9.931531
3      0.011859 -0.027938       5        1   8.026737
9      0.032369  0.040528       6        1   6.822297
6      0.041028 -0.027632       7        1   5.334337
7      0.007937  0.105817       8        1   5.156641
5      0.013094 -0.155523       9        1   5.097232
1     -0.228187  0.020472      10        1   3.940675, topic_info=      Term         Freq        Total Category  logprob  loglift
20    love  6409.000000  6409.000000  Default  30.0000  30.0000
766     la   827.000000   827.000000  Default  29.0000  29.0000
25      oh  3315.000000  3315.000000  Default  28.0000  28.0000
99    rock  1433.000000  1433.000000  Default  27.0000  27.0000
2101   jam   409.000000   409.000000  Default  26.0000  26.0000
...    ...          ...          ...      ...      ...      ...
113   turn    55.352452   955.162723  Topic10  -5.3264   0.3857
13      go    58.763036  3064.731047  Topic10  -5.2666  -0.7204
25      oh    55.788637  3315.740665  Topic10  -5.3185  -0.8510
34      to    53.104819  2250.452846  Topic10  -5.3678  -0.5128
281   beat    45.457925   762.904094  Topic10  -5.5233   0.4135

[796 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
4631       4  0.078196     acid
4631       6  0.821054     acid
4631       8  0.078196     acid
11936      6  0.988751  acieeed
3321       2  0.021214      add
...      ...       ...      ...
755        6  0.044233     zone
755        9  0.011058     zone
755       10  0.829362     zone
1285       3  0.060796     zulu
1285       4  0.851141     zulu

[2664 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 1, 5, 9, 4, 10, 7, 8, 6, 2])

In [51]:
lda_1990 = lda_models.lda_info(1990)

Perplexity:  -7.62350670287913
Coherence:  0.36570174531398286


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2576 samples in 0.003s...
[t-SNE] Computed neighbors for 2576 samples in 0.161s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2576
[t-SNE] Computed conditional probabilities for sample 2000 / 2576
[t-SNE] Computed conditional probabilities for sample 2576 / 2576
[t-SNE] Mean sigma: 0.002276


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 62.152462
[t-SNE] KL divergence after 1000 iterations: 0.495648


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [52]:
lda_1990

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5     -0.064721  0.008375       1        1  26.081427
1      0.043475 -0.119356       2        1  15.881197
3      0.032169 -0.017989       3        1  11.237602
9      0.026070  0.047463       4        1  11.112265
4      0.020811 -0.016505       5        1   8.563141
2     -0.056929  0.094627       6        1   7.343765
6      0.078149  0.109842       7        1   5.665173
0      0.012112  0.011688       8        1   5.198932
7     -0.183290 -0.047069       9        1   4.623340
8      0.092155 -0.071075      10        1   4.293158, topic_info=       Term         Freq        Total Category  logprob  loglift
166    love  4127.000000  4127.000000  Default  30.0000  30.0000
134    baby  1880.000000  1880.000000  Default  29.0000  29.0000
174      oh  2286.000000  2286.000000  Default  28.0000  28.0000
2630     la   312.000000   312.000000  Default  27.0000  27.0000
436   chase   287.000000   287.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
192      to    56.366970  1605.397603  Topic10  -5.4421  -0.2011
13     like    56.918277  3339.584302  Topic10  -5.4324  -0.9238
1251   real    47.345153   562.809300  Topic10  -5.6166   0.6727
159    head    45.597679   676.012090  Topic10  -5.6542   0.4518
191    time    41.557948  2204.469678  Topic10  -5.7469  -0.8230

[790 rows x 6 columns], token_table=       Topic      Freq    Term
term                          
5618       3  0.982541   aaqil
12263      2  0.930293   adapt
1052       9  0.964669   admin
4015       2  0.916651  adonai
1053       4  0.066537  africa
...      ...       ...     ...
403       10  0.138795      yo
15612      5  0.940796   zerop
1301       9  0.958224   zomba
1883       1  0.950903  zurich
15203      1  0.947657    über

[2741 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 2, 4, 10, 5, 3, 7, 1, 8, 9])

In [53]:
lda_2000 = lda_models.lda_info(2000)

Perplexity:  -7.724922138087677
Coherence:  0.34721749768837984


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2571 samples in 0.003s...
[t-SNE] Computed neighbors for 2571 samples in 0.156s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2571
[t-SNE] Computed conditional probabilities for sample 2000 / 2571
[t-SNE] Computed conditional probabilities for sample 2571 / 2571
[t-SNE] Mean sigma: 0.004272


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 66.907181
[t-SNE] KL divergence after 1000 iterations: 0.563375


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [54]:
lda_2000

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3     -0.118271  0.012866       1        1  16.249665
2      0.079110  0.004776       2        1  15.275050
5      0.005733  0.040223       3        1  14.025049
1      0.031255  0.015482       4        1  11.792932
7      0.008055  0.103410       5        1  11.710289
8      0.077427  0.013529       6        1   7.700374
9      0.070617 -0.017588       7        1   7.292648
0     -0.130769 -0.014000       8        1   6.507386
4     -0.031817  0.016446       9        1   6.503133
6      0.008660 -0.175144      10        1   2.943474, topic_info=       Term         Freq        Total Category  logprob  loglift
352      la   813.000000   813.000000  Default  30.0000  30.0000
137      oh  2325.000000  2325.000000  Default  29.0000  29.0000
39     love  2874.000000  2874.000000  Default  28.0000  28.0000
118      go  2548.000000  2548.000000  Default  27.0000  27.0000
158      to  1596.000000  1596.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
1662  knock    25.689028   194.743312  Topic10  -5.8776   1.5000
196    know    35.602282  3992.956560  Topic10  -5.5512  -1.1943
17      eye    29.376972   907.611973  Topic10  -5.7434   0.0950
788    lord    26.166242   266.973150  Topic10  -5.8592   1.2029
114     get    26.258607  3031.749553  Topic10  -5.8557  -1.2233

[793 rows x 6 columns], token_table=       Topic      Freq      Term
term                            
9392       2  0.985749      aang
9392       3  0.003881      aang
3467       1  0.033812  accident
3467       3  0.879111  accident
3467       6  0.067624  accident
...      ...       ...       ...
3741       1  0.022255       zen
3741       2  0.244806       zen
3741       6  0.712164       zen
5288       4  0.944828      zeta
12278      2  0.932757      zuko

[2597 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 3, 6, 2, 8, 9, 10, 1, 5, 7])

In [55]:
lda_2010 = lda_models.lda_info(2010)

Perplexity:  -7.521918854052374
Coherence:  0.355117462883238


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2588 samples in 0.003s...
[t-SNE] Computed neighbors for 2588 samples in 0.105s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2588
[t-SNE] Computed conditional probabilities for sample 2000 / 2588
[t-SNE] Computed conditional probabilities for sample 2588 / 2588
[t-SNE] Mean sigma: 0.002485


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 62.830887
[t-SNE] KL divergence after 1000 iterations: 0.500625


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [56]:
lda_2010

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5     -0.020803  0.053512       1        1  24.648636
2     -0.059138 -0.103575       2        1  24.588843
8     -0.018730  0.122093       3        1  11.921447
9     -0.026415 -0.006354       4        1   7.640362
1     -0.056479 -0.045353       5        1   7.388017
3     -0.032425  0.078948       6        1   7.363341
7     -0.027969 -0.088868       7        1   5.246931
6     -0.003694 -0.032898       8        1   4.785539
4      0.005771  0.046551       9        1   3.526450
0      0.239881 -0.024055      10        1   2.890434, topic_info=      Term         Freq        Total Category  logprob  loglift
13      oh  2650.000000  2650.000000  Default  30.0000  30.0000
154   yeah  3502.000000  3502.000000  Default  29.0000  29.0000
142     to  1967.000000  1967.000000  Default  28.0000  28.0000
54    know  5227.000000  5227.000000  Default  27.0000  27.0000
108    get  5293.000000  5293.000000  Default  26.0000  26.0000
...    ...          ...          ...      ...      ...      ...
1172     n    30.818055   120.486050  Topic10  -5.8087   2.1803
143    toe    30.028577   110.041398  Topic10  -5.8346   2.2451
7     like    46.284813  6500.706085  Topic10  -5.4019  -1.4011
87    baby    38.831817  1208.778742  Topic10  -5.5775   0.1056
521   live    29.880948   967.048221  Topic10  -5.8395   0.0667

[810 rows x 6 columns], token_table=       Topic      Freq      Term
term                            
15038      1  0.952995      aaah
13712      9  0.843235     abasi
10564      4  0.811149  abundant
10564      7  0.081115  abundant
10564      8  0.081115  abundant
...      ...       ...       ...
18473      9  0.785323  настанет
18477      9  0.785336  ожидании
18484      9  0.785287       тот
18486      9  0.785194       час
18204      4  0.803668         돼

[2667 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 3, 9, 10, 2, 4, 8, 7, 5, 1])

In [57]:
lda_2020 = lda_models.lda_info(2020)

Perplexity:  -7.41445938271376
Coherence:  0.3140701002227656


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2571 samples in 0.003s...
[t-SNE] Computed neighbors for 2571 samples in 0.153s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2571
[t-SNE] Computed conditional probabilities for sample 2000 / 2571
[t-SNE] Computed conditional probabilities for sample 2571 / 2571
[t-SNE] Mean sigma: 0.003297


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 64.779175
[t-SNE] KL divergence after 1000 iterations: 0.554316


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [58]:
lda_2020

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
6      0.075527 -0.043675       1        1  25.443752
3     -0.086325 -0.004720       2        1  23.073907
0     -0.095441 -0.011683       3        1   9.653256
5      0.023069 -0.116052       4        1   7.111365
9     -0.010343  0.049949       5        1   7.032642
2     -0.085248 -0.010701       6        1   6.408622
4      0.151623 -0.011994       7        1   6.397123
1     -0.007932  0.068466       8        1   5.734944
7     -0.018595 -0.029118       9        1   4.612612
8      0.053665  0.109529      10        1   4.531777, topic_info=       Term         Freq        Total Category  logprob  loglift
250      oh  3296.000000  3296.000000  Default  30.0000  30.0000
32    wanna  2462.000000  2462.000000  Default  29.0000  29.0000
34     yeah  5627.000000  5627.000000  Default  28.0000  28.0000
1135    ooh  1181.000000  1181.000000  Default  27.0000  27.0000
271   bitch  2669.000000  2669.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
586    tell    61.549391  2151.666213  Topic10  -5.5989  -0.4601
212     try    52.291250  1200.726894  Topic10  -5.7619  -0.0398
610    want    55.071191  2536.249586  Topic10  -5.7101  -0.7358
232    away    50.808344   803.021251  Topic10  -5.7906   0.3337
30       to    53.301603  2007.206523  Topic10  -5.7427  -0.5345

[821 rows x 6 columns], token_table=       Topic      Freq       Term
term                             
5427       1  0.168034        aah
5427       4  0.784159        aah
8507       5  0.890689    academy
7953       1  0.931265       acme
263        1  0.012095         ah
...      ...       ...        ...
12202      3  0.874963         yé
12367      4  0.805828  zillakami
12203      3  0.874934        zum
1813       3  0.931504       zuma
9360       5  0.890441    écoutez

[2792 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[7, 4, 1, 6, 10, 3, 5, 2, 8, 9])

Basic LDA model give us our baseline, we've got this default **perspicacity** and **coherence** score. Let's try to improve this to score and also our qualitative intuition about topic. As we saw topic seems really similar over the decade and it's quite difficult to retrieve some good topics given the representation we compute. 

# Improve the preprocessing

In this part, we will try to create a pre-processing function that can take into account bigrams and trigrams and also allow to put aside the terms that could have been too recurrent in the previous part.

## ngram recognition with gensim

A way to improve lyrics comprehension is to use bigram and trigram with the help of phraser in gensim.

In [59]:
import gensim

def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

# process in lyrics into words
data = sdf['lyrics'].tolist()
data_words = list(sent_to_words(data))

In [60]:
# display the result
data_words[0][:10]

['animal',
 'animal',
 'animal',
 'animal',
 'animal',
 'animal',
 'animal',
 'why',
 'don',
 'you']

In [61]:
import gensim

# Build the bigram and trigram models
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_model = gensim.models.phrases.Phraser(bigram)
trigram_model = gensim.models.phrases.Phraser(trigram)

In [62]:
from numpy.random import randint, seed

# set seed from numpy
seed(18)

# draw the upper bound
upper_bound = randint(len(data_words))

# display a random example
print('bigram model: ', bigram_model[data_words[upper_bound]])
print('\ntrigram model: ', bigram_model[data_words[upper_bound]])
print('\nsentence: ',' '.join(data_words[upper_bound]))

bigram model:  ['beautiful', 'brother', 'of', 'mine', 'whatever', 'may', 'be', 'your', 'birth', 'sign', 'we', 'are', 'not', 'of', 'the', 'same', 'seed', 'although', 'we', 'are', 'both', 'the', 'same', 'breed', 'together', 'we', 're', 'truly', 'black', 'power', 'power', 'learning', 'to', 'trust', 'by', 'the', 'hour', 'hour', 'loving', 'our', 'women', 'now', 'more', 'we', 'love', 'more', 'respecting', 'what', 'black', 'is', 'now', 'for', 'and', 'we', 've', 'got', 'love', 'we', 've', 'got', 'love', 'we', 've', 'got', 'love', 'we', 'got', 'love', 'we', 've', 'got', 'love', 'we', 'got', 'love', 'beautiful', 'sister', 'of', 'mine', 'glad', 'we', 'both', 'think', 'it', 'now', 'time', 'to', 'really', 'show', 'what', 'we', 'can', 'do', 'improving', 'black', 'pride', 'is', 'now', 'true', 'at', 'last', 'we', 've', 'outgrown', 'uncle_tom', 'uncle_tom', 'devoting', 'more', 'time', 'in', 'the', 'slum', 'in', 'the', 'slum', 'showing', 'our', 'own', 'new', 'pride', 'we', 'have', 'pride', 'that', 'make

We are able to see some bigram and bigram, most of the time it's a words with its adjective or a group of onomatopeia.

As previously explained, we would also like to set aside irrelevant terms that may have been recurrent in our last analysis. If we look at the previous bar charts, we can observe a significant amount of these last terms over all the decades. This is the case for example of like, know or yeah. Most of the time these terms qualified as uninteresting are verbs or onomatopoeias. Let's try to identify the less interesting ones by comparing the bar charts with the visualizations of pyLDAvis. We can notice a strong recurrence of the verbs like, know, come, get which are not necessarily relevant because they are found in most of the analyzed topics. We can also find onomatopoeias oh, yeah and la in most of the topics.

In [63]:
# list recurrent terms
recurrent_terms = {'like','know','come','get', 'got','go','to','oh','yeah','la'}


# default preprocessing
def ngram_preprocess(text, nlp = new_nlp,
                     bigram = bigram_model,
                     trigram = trigram_model,
                    new_stopwords = recurrent_terms):
    
    # perform basic preprocessing to transform sentence to list of words
    words = gensim.utils.simple_preprocess(text)
    
    # customize stopwords
    spacy_stopwords = new_nlp.Defaults.stop_words
    ext_stopwords = spacy_stopwords | new_stopwords # union of set
    
    #removing stop words
    no_stop_words = [word for word in words if word not in ext_stopwords]
    
    # perform bigram model
    bigram_words = bigram[no_stop_words]
    
    # perform trigram model
    trigram_words = trigram[bigram_words]
    
    # recreate the sentence
    sentence = ' '.join(trigram_words)
    
    #tokenization to get lemma
    tokens = [token for token in nlp(sentence)]
    
    #LEMMATISATION and filter alphanumeric characters
    sentence = [word.lemma_ for word in tokens if word.text.isalpha()]

    return sentence

In [64]:
# test with the previously draw sentence
ngram_preprocess(' '.join(data_words[upper_bound]))[:10]

['beautiful',
 'brother',
 'birth',
 'sign',
 'seed',
 'breed',
 'truly',
 'black',
 'power',
 'power']

Let's try to rerun LDA with the new preprocessing function 

In [65]:
ngram_model = LDATopicModeling(decade = 2000, lang_preprocess = ngram_preprocess)

100%|██████████| 2611/2611 [00:00<00:00, 5598.62it/s]


In [66]:
ngram_model.dashboard_LDAvis()

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
7      0.178784  0.057699       1        1  17.461204
5     -0.051046 -0.078770       2        1  15.365419
0     -0.126361  0.073256       3        1  13.271933
8      0.022290 -0.015750       4        1  12.306393
2     -0.008340 -0.099695       5        1  10.361394
1      0.023596 -0.097160       6        1   8.300316
4      0.109230  0.007158       7        1   5.965658
3     -0.084899  0.010156       8        1   5.801452
6     -0.018587  0.122891       9        1   5.594882
9     -0.044668  0.020215      10        1   5.571351, topic_info=       Term         Freq        Total Category  logprob  loglift
39     love  2745.000000  2745.000000  Default  30.0000  30.0000
108     don  3822.000000  3822.000000  Default  29.0000  29.0000
162   wanna   993.000000   993.000000  Default  28.0000  28.0000
120      go  2369.000000  2369.000000  Default  27.0000  27.0000
1172  nigga   615.000000   615.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
664     god    59.414057   696.627782  Topic10  -5.6118   0.4258
222    well    59.848289   792.332331  Topic10  -5.6046   0.3044
132      ll    68.176898  2624.492994  Topic10  -5.4743  -0.7630
155    tell    63.063015  1313.533036  Topic10  -5.5522  -0.1488
39     love    67.771981  2745.561251  Topic10  -5.4802  -0.8141

[816 rows x 6 columns], token_table=       Topic      Freq        Term
term                              
17540      4  0.848505          aa
9577       2  0.996745        aang
17617      2  0.870581      abhore
7056       9  0.756394     abigail
12766      3  0.094171  accustomed
...      ...       ...         ...
16939      7  0.960012       zelda
3769       6  0.988184         zen
5360       6  0.958964        zeta
5361       6  0.924982       zetas
12573      3  0.966967        zuko

[2658 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[8, 6, 1, 9, 3, 2, 5, 4, 7, 10])

In [67]:
ngram_model.plot_tsne()

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2539 samples in 0.003s...
[t-SNE] Computed neighbors for 2539 samples in 0.133s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2539
[t-SNE] Computed conditional probabilities for sample 2000 / 2539
[t-SNE] Computed conditional probabilities for sample 2539 / 2539
[t-SNE] Mean sigma: 0.007436


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] KL divergence after 250 iterations with early exaggeration: 69.108307
[t-SNE] KL divergence after 1000 iterations: 0.643453


Loading BokehJS ...

In [68]:
ngram_model = LDATopicModeling(decade = 2000,
                               lang_preprocess = ngram_preprocess,
                              cross_valid = True, epochs = 10)

total lda computation:  18
coherence: 0.33489674184535667
alpha: symmetric
eta: symmetric
topic: 2
coherence: 0.38592913363595605
alpha: asymmetric
eta: symmetric
topic: 2
coherence: 0.32876772075833516
alpha: symmetric
eta: symmetric
topic: 3
coherence: 0.3347526773811737
alpha: asymmetric
eta: symmetric
topic: 3
coherence: 0.34632884492259897
alpha: symmetric
eta: symmetric
topic: 4
coherence: 0.3284252748245064
alpha: asymmetric
eta: symmetric
topic: 4
coherence: 0.33929485865651554
alpha: symmetric
eta: symmetric
topic: 5
coherence: 0.3280032771407379
alpha: asymmetric
eta: symmetric
topic: 5
coherence: 0.30577232863665743
alpha: symmetric
eta: symmetric
topic: 6
coherence: 0.33044353448549296
alpha: asymmetric
eta: symmetric
topic: 6
coherence: 0.29943956439107894
alpha: symmetric
eta: symmetric
topic: 7
coherence: 0.3235262662598446
alpha: asymmetric
eta: symmetric
topic: 7
coherence: 0.3204302238221843
alpha: symmetric
eta: symmetric
topic: 8
coherence: 0.3067357330736096
alpha:

In [69]:
ngram_model.plot_coherence('alpha')

In [70]:
ngram_model.plot_coherence('eta')

In [71]:
ngram_model.plot_tsne()

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.042s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000087
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.646801
[t-SNE] KL divergence after 1000 iterations: 0.206112


Loading BokehJS ...

In [72]:
ngram_model.dashboard_LDAvis()

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



PreparedData(topic_coordinates=             x    y  topics  cluster       Freq
topic                                          
0      0.07003  0.0       1        1  62.476873
1     -0.07003  0.0       2        1  37.523127, topic_info=       Term         Freq        Total Category  logprob  loglift
89      ain  1305.000000  1305.000000  Default  30.0000  30.0000
750     man  1646.000000  1646.000000  Default  29.0000  29.0000
1172  nigga   567.000000   567.000000  Default  28.0000  28.0000
532    fuck   751.000000   751.000000  Default  27.0000  27.0000
211    shit   703.000000   703.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
262     say   364.190603  1008.600521   Topic2  -5.7060  -0.0384
158      to   403.379604  1534.416497   Topic2  -5.6038  -0.3558
77     time   432.599236  2235.131263   Topic2  -5.5339  -0.6620
156   think   389.756771  1404.844891   Topic2  -5.6382  -0.3019
133    look   359.055484  1207.202896   Topic2  -5.7202  -0.2324

[205 rows x 6 columns], token_table=       Topic      Freq   Term
term                         
9577       1  0.987417   aang
9577       2  0.012241   aang
89         1  0.222899    ain
89         2  0.776701    ain
10262      1  0.042250     ak
...      ...       ...    ...
3156       2  0.982891    yuh
16939      1  0.043942  zelda
16939      2  0.966722  zelda
3769       1  0.022892    zen
3769       2  0.984343    zen

[317 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [73]:
lda_cv_models = LDAPipeline(prep = ngram_preprocess, cv = True)

total lda computation:  18
coherence: 0.3483242262225434
alpha: symmetric
eta: symmetric
topic: 2
coherence: 0.3541359150892269
alpha: asymmetric
eta: symmetric
topic: 2
coherence: 0.3339099782037911
alpha: symmetric
eta: symmetric
topic: 3
coherence: 0.3532551364655984
alpha: asymmetric
eta: symmetric
topic: 3
coherence: 0.34537428557404815
alpha: symmetric
eta: symmetric
topic: 4
coherence: 0.3331298989017937
alpha: asymmetric
eta: symmetric
topic: 4
coherence: 0.3380812821135202
alpha: symmetric
eta: symmetric
topic: 5
coherence: 0.3510664492013623
alpha: asymmetric
eta: symmetric
topic: 5
coherence: 0.3202052533652072
alpha: symmetric
eta: symmetric
topic: 6
coherence: 0.3366565195218458
alpha: asymmetric
eta: symmetric
topic: 6
coherence: 0.33477173321951176
alpha: symmetric
eta: symmetric
topic: 7
coherence: 0.3277255889797041
alpha: asymmetric
eta: symmetric
topic: 7
coherence: 0.3224929210082502
alpha: symmetric
eta: symmetric
topic: 8
coherence: 0.33782573656787473
alpha: asym

In [74]:
lda_cv_models.get_metrics()

decade  coherence  perplexity
0    1960   0.354136   -7.171939
1    1970   0.435095   -7.026951
2    1980   0.409733   -7.244499
3    1990   0.407901   -7.729087
4    2000   0.358789   -7.781129
5    2010   0.402500   -7.616403
6    2020   0.391414   -7.543440

In [75]:
lda_cv_1960 = lda_cv_models.lda_info(1960)

Perplexity:  -7.171939203963953
Coherence:  0.3541359150892269


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.041s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000081
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.681534
[t-SNE] KL divergence after 1000 iterations: 0.207166


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [76]:
lda_cv_1960

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0      0.089539  0.0       1        1  64.871156
1     -0.089539  0.0       2        1  35.128844, topic_info=       Term         Freq        Total Category  logprob  loglift
9      love  5877.000000  5877.000000  Default  30.0000  30.0000
17     baby  3152.000000  3152.000000  Default  29.0000  29.0000
528   black   351.000000   351.000000  Default  28.0000  28.0000
62       to  1432.000000  1432.000000  Default  27.0000  27.0000
4529    jem   239.000000   239.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
14      way   229.065845  1422.925556   Topic2  -5.7877  -0.7803
594     hey   198.660481   677.517298   Topic2  -5.9301  -0.1807
199    tell   226.389211  1523.704560   Topic2  -5.7995  -0.8605
122    want   201.995475  1430.095878   Topic2  -5.9135  -0.9111
51     girl   199.613950  1269.540860   Topic2  -5.9254  -0.8039

[192 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
12379      1  0.998312  abilene
1638       1  0.042899   africa
1638       2  0.986680   africa
1639       1  0.022819  african
1639       2  0.981200  african
...      ...       ...      ...
590        2  0.934810   yellow
206        1  0.849595      yes
206        2  0.150226      yes
733        1  0.367151    young
733        2  0.630879    young

[294 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [77]:
lda_cv_1970 = lda_cv_models.lda_info(1970)

Perplexity:  -7.026950613459042
Coherence:  0.4350950299107389


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.036s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000415
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.350746
[t-SNE] KL divergence after 1000 iterations: 0.212509


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [78]:
lda_cv_1970

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0      0.065293  0.0       1        1  55.673677
1     -0.065293  0.0       2        1  44.326323, topic_info=      Term         Freq        Total Category  logprob  loglift
156   love  6890.000000  6890.000000  Default  30.0000  30.0000
277   baby  2957.000000  2957.000000  Default  29.0000  29.0000
145    don  3510.000000  3510.000000  Default  28.0000  28.0000
233   need  1298.000000  1298.000000  Default  27.0000  27.0000
420  wanna   956.000000   956.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
156   love   620.812206  6890.023234   Topic2  -5.0624  -1.5932
159  right   386.862889  1177.107039   Topic2  -5.5353  -0.2992
434  thing   385.672466  1209.282027   Topic2  -5.5384  -0.3292
403   tell   396.896316  1490.914534   Topic2  -5.5097  -0.5099
298   good   355.940095  1492.035642   Topic2  -5.6186  -0.6195

[209 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
775       1  0.027676  africa
775       2  0.968665  africa
721       1  0.780990     ain
721       2  0.219452     ain
8097      1  0.044983   annie
...     ...       ...     ...
675       2  0.892853    wind
1368      1  0.092541    wing
1368      2  0.913840    wing
720       1  0.911430      ya
720       2  0.087180      ya

[318 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [79]:
lda_cv_1980 = lda_cv_models.lda_info(1980)

Perplexity:  -7.244498526795922
Coherence:  0.4097330909303903


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2610 samples in 0.002s...
[t-SNE] Computed neighbors for 2610 samples in 0.043s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2610
[t-SNE] Computed conditional probabilities for sample 2000 / 2610
[t-SNE] Computed conditional probabilities for sample 2610 / 2610
[t-SNE] Mean sigma: 0.000640
[t-SNE] KL divergence after 250 iterations with early exaggeration: 52.454788
[t-SNE] KL divergence after 1000 iterations: 0.278725


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [80]:
lda_cv_1980

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.063033  0.050386       1        1  41.476182
0     -0.035693 -0.060634       2        1  32.572455
2      0.098727  0.010248       3        1  25.951363, topic_info=       Term         Freq        Total Category  logprob  loglift
98     rock  1337.000000  1337.000000  Default  30.0000  30.0000
20     love  6033.000000  6033.000000  Default  29.0000  29.0000
37     baby  2582.000000  2582.000000  Default  28.0000  28.0000
283    beat   743.000000   743.000000  Default  27.0000  27.0000
90    party   486.000000   486.000000  Default  26.0000  26.0000
..      ...          ...          ...      ...      ...      ...
91   people   252.033159   776.982592   Topic3  -5.6089   0.2231
62     girl   292.296338  1595.730237   Topic3  -5.4607  -0.3484
113    want   308.584726  2256.487631   Topic3  -5.4065  -0.6406
111    turn   252.166079   959.348527   Topic3  -5.6084   0.0128
314    feel   280.302402  1938.609181   Topic3  -5.5026  -0.5849

[273 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
281       3  0.982706    ace
9256      1  0.988265     ag
9256      3  0.012201     ag
131       1  0.145083     ah
131       2  0.361624     ah
...     ...       ...    ...
903       2  0.087038     yo
903       3  0.889031     yo
744       1  0.254673  young
744       2  0.162065  young
744       3  0.585417  young

[493 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1, 3])

In [81]:
lda_cv_1990 = lda_cv_models.lda_info(1990)

Perplexity:  -7.729082336625409
Coherence:  0.40790140460917135


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2605 samples in 0.002s...
[t-SNE] Computed neighbors for 2605 samples in 0.063s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2605
[t-SNE] Computed conditional probabilities for sample 2000 / 2605
[t-SNE] Computed conditional probabilities for sample 2605 / 2605
[t-SNE] Mean sigma: 0.000913
[t-SNE] KL divergence after 250 iterations with early exaggeration: 57.267273
[t-SNE] KL divergence after 1000 iterations: 0.372078


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [82]:
lda_cv_1990

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.109663 -0.034054       1        1  30.821396
1     -0.046796 -0.012466       2        1  24.788042
0      0.009116  0.010143       3        1  19.048852
4      0.018184  0.082080       4        1  15.930336
3      0.129158 -0.045703       5        1   9.411374, topic_info=      Term         Freq        Total Category  logprob  loglift
145   love  4369.000000  4369.000000  Default  30.0000  30.0000
636   fuck   505.000000   505.000000  Default  29.0000  29.0000
248   shit   600.000000   600.000000  Default  28.0000  28.0000
229  nigga   502.000000   502.000000  Default  27.0000  27.0000
631  bitch   322.000000   322.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
141    let    91.047272  1826.686152   Topic5  -5.6654  -0.6356
300     go    93.123487  2349.134103   Topic5  -5.6428  -0.8646
19    tell    88.053216  1443.070857   Topic5  -5.6988  -0.4333
408  thing    82.042272  1185.247585   Topic5  -5.7695  -0.3072
112   baby    83.468449  1846.218125   Topic5  -5.7523  -0.7332

[443 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
12372      3  0.037718    aaron
12372      4  0.113155    aaron
12372      5  0.829801    aaron
2213       1  0.081582  african
2213       2  0.843019  african
...      ...       ...      ...
378        3  0.446668       yo
378        4  0.214653       yo
378        5  0.195713       yo
15884      3  0.914162    zerop
15466      4  0.960492     über

[1003 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 2, 1, 5, 4])

In [83]:
lda_cv_2000 = lda_cv_models.lda_info(2000)

Perplexity:  -7.781129537532919
Coherence:  0.35878949047147957


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.001s...
[t-SNE] Computed neighbors for 2611 samples in 0.037s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000105
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.578671
[t-SNE] KL divergence after 1000 iterations: 0.206774


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [84]:
lda_cv_2000

PreparedData(topic_coordinates=             x    y  topics  cluster       Freq
topic                                          
0      0.06639  0.0       1        1  58.638616
1     -0.06639  0.0       2        1  41.361384, topic_info=       Term         Freq        Total Category  logprob  loglift
89      ain  1300.000000  1300.000000  Default  30.0000  30.0000
1172  nigga   563.000000   563.000000  Default  29.0000  29.0000
532    fuck   745.000000   745.000000  Default  28.0000  28.0000
211    shit   698.000000   698.000000  Default  27.0000  27.0000
605     hey   768.000000   768.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
262     say   425.523602  1007.272864   Topic2  -5.6478   0.0211
77     time   499.503721  2242.949204   Topic2  -5.4875  -0.6191
163    want   462.791756  1685.974221   Topic2  -5.5638  -0.4100
1085     ve   411.358865  1668.290387   Topic2  -5.6816  -0.5173
232    girl   385.515309   877.667779   Topic2  -5.7465   0.0601

[210 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
9577       1  0.994743  aang
9577       2  0.004044  aang
170        1  0.160230    ah
170        2  0.839020    ah
89         1  0.218371   ain
...      ...       ...   ...
12571      1  0.980342  ying
421        1  0.107908    yo
421        2  0.893376    yo
3156       1  0.029098   yuh
3156       2  0.989317   yuh

[327 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [85]:
lda_cv_2010 = lda_cv_models.lda_info(2010)

Perplexity:  -7.616403033438797
Coherence:  0.40250031771861566


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2610 samples in 0.001s...
[t-SNE] Computed neighbors for 2610 samples in 0.040s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2610
[t-SNE] Computed conditional probabilities for sample 2000 / 2610
[t-SNE] Computed conditional probabilities for sample 2610 / 2610
[t-SNE] Mean sigma: 0.000475
[t-SNE] KL divergence after 250 iterations with early exaggeration: 53.056549
[t-SNE] KL divergence after 1000 iterations: 0.276887


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [86]:
lda_cv_2010

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2      0.106201  0.008043       1        1  39.324335
1     -0.039783 -0.052125       2        1  35.182547
0     -0.066418  0.044082       3        1  25.493119, topic_info=       Term         Freq        Total Category  logprob  loglift
333   bitch  1972.000000  1972.000000  Default  30.0000  30.0000
902   nigga  1254.000000  1254.000000  Default  29.0000  29.0000
903  niggas  1097.000000  1097.000000  Default  28.0000  28.0000
468    shit  1766.000000  1766.000000  Default  27.0000  27.0000
8      love  3230.000000  3230.000000  Default  26.0000  26.0000
..      ...          ...          ...      ...      ...      ...
125   leave   299.377698  1217.856340   Topic3  -5.6446  -0.0364
133     say   287.496116  1144.478039   Topic3  -5.6851  -0.0147
54     look   296.873981  1466.091498   Topic3  -5.6530  -0.2303
114      go   329.639341  2497.409873   Topic3  -5.5483  -0.6582
17    thing   267.832434   976.647712   Topic3  -5.7560   0.0730

[285 rows x 6 columns], token_table=       Topic      Freq   Term
term                         
1009       1  0.904849      I
1009       2  0.040718      I
1009       3  0.054291      I
1406       1  0.900740      a
1406       2  0.089386      a
...      ...       ...    ...
827        3  0.063621     yo
18236      2  0.922382  yooou
247        1  0.978651    yuh
247        2  0.014048    yuh
247        3  0.009365    yuh

[537 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 2, 1])

In [87]:
lda_cv_2020 = lda_cv_models.lda_info(2020)

Perplexity:  -7.543440004951669
Coherence:  0.391414232140715


/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:986: FutureWarning:

The PCA initialization in TSNE will change to have the standard deviation of PC1 equal to 1e-4 in 1.2. This will ensure better convergence.



[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 2611 samples in 0.002s...
[t-SNE] Computed neighbors for 2611 samples in 0.037s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2611
[t-SNE] Computed conditional probabilities for sample 2000 / 2611
[t-SNE] Computed conditional probabilities for sample 2611 / 2611
[t-SNE] Mean sigma: 0.000089
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.392559
[t-SNE] KL divergence after 1000 iterations: 0.206876


Loading BokehJS ...

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:248: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only



In [88]:
lda_cv_2020

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0      0.064566  0.0       1        1  58.500467
1     -0.064566  0.0       2        1  41.499533, topic_info=      Term         Freq        Total Category  logprob  loglift
273  bitch  2736.000000  2736.000000  Default  30.0000  30.0000
298   fuck  2293.000000  2293.000000  Default  29.0000  29.0000
139   love  3678.000000  3678.000000  Default  28.0000  28.0000
354     uh  1213.000000  1213.000000  Default  27.0000  27.0000
327  nigga  1223.000000  1223.000000  Default  26.0000  26.0000
..     ...          ...          ...      ...      ...      ...
522   talk   443.117473   934.450149   Topic2  -5.7562   0.1334
587   tell   512.143592  2070.855813   Topic2  -5.6114  -0.5176
248   look   473.005743  1501.258090   Topic2  -5.6909  -0.2755
29    time   492.643994  2423.989838   Topic2  -5.6502  -0.7139
707    say   450.551135  1381.566075   Topic2  -5.7395  -0.2410

[205 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
0         1  0.236313      I
0         2  0.764204      I
265       1  0.219057     ah
265       2  0.781111     ah
266       1  0.391829    ain
...     ...       ...    ...
34        2  0.109244   wish
231       1  0.826446  world
231       2  0.173682  world
366       1  0.183138     yo
366       2  0.815983     yo

[319 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2])

In [89]:
lda_cv_models.get_metrics()

decade  coherence  perplexity
0    1960   0.354136   -7.171939
1    1970   0.435095   -7.026951
2    1980   0.409733   -7.244498
3    1990   0.407901   -7.729071
4    2000   0.358789   -7.781130
5    2010   0.402500   -7.616402
6    2020   0.391414   -7.543440

## References

- Genius data: https://www.kaggle.com/datasets/carlosgdcj/genius-song-lyrics-with-language-information

- Gensim doc: https://radimrehurek.com/gensim/models/ldamodel.html

- Example of use:
  - https://neptune.ai/blog/pyldavis-topic-modelling-exploration-tool-that-every-nlp-data-scientist-should-know

  - https://medium.com/analytics-vidhya/topic-modelling-using-word-embeddings-and-latent-dirichlet-allocation-3494778307bc

  - https://towardsdatascience.com/evaluate-topic-model-in-python-latent-dirichlet-allocation-lda-7d57484bb5d0

